# Eat Safe, Love

## Notebook Set Up

In [1]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint
import pandas as pd

In [2]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [3]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [4]:
# review the collections in our database
print(db.list_collection_names())

['establishments']


In [5]:
# assign the collection to a variable
establishments = db['establishments']

## Part 3: Exploratory Analysis
Unless otherwise stated, for each question: 
* Use `count_documents` to display the number of documents contained in the result.
* Display the first document in the results using `pprint`.
* Convert the result to a Pandas DataFrame, print the number of rows in the DataFrame, and display the first 10 rows.

### 1. Which establishments have a hygiene score equal to 20?

In [6]:
# Find the establishments with a hygiene score of 20
query = {'scores.Hygiene': 20}

# Use count_documents to display the number of documents in the result
results = establishments.find(query)
print(f'There are {db.establishments.count_documents(query)} establishments with a hygiene score of 20')

print('------------------------------------------------------------')
# Display the first document in the results using pprint

pprint(results[0])
    


There are 41 establishments with a hygiene score of 20
------------------------------------------------------------
{'AddressLine1': '5-6 Southfields Road',
 'AddressLine2': 'Eastbourne',
 'AddressLine3': 'East Sussex',
 'AddressLine4': '',
 'BusinessName': 'The Chase Rest Home',
 'BusinessType': 'Caring Premises',
 'BusinessTypeID': 5,
 'ChangesByServerID': 0,
 'Distance': 4613.888288172291,
 'FHRSID': 110681,
 'LocalAuthorityBusinessID': '4029',
 'LocalAuthorityCode': '102',
 'LocalAuthorityEmailAddress': 'Customerfirst@eastbourne.gov.uk',
 'LocalAuthorityName': 'Eastbourne',
 'LocalAuthorityWebSite': 'http://www.eastbourne.gov.uk/foodratings',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'BN21 1BU',
 'RatingDate': '2021-09-23T00:00:00',
 'RatingKey': 'fhrs_0_en-gb',
 'RatingValue': 0,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('64979bb5667ad5b134bd871f'),
 'geocode': {'latitude': 50.769705, 'longitude': 0.27694},
 'links': [{'href': 'https://api.ratings.f

In [7]:
# Convert the result to a Pandas DataFrame
#Creating list from keys and values in dictionary results
inputdict = results[0]
columns = list(inputdict.keys())
values_list = list(inputdict.values())
#converting list to DataFrame
establishments_df = pd.DataFrame(values_list,columns)
# Display the number of rows in the DataFrame
print(f'There are {len(establishments_df.index)} rows in the DataFrame')
print('------------------------------------------------------')
# Display the first 10 rows of the DataFrame
establishments_df.head(10)

There are 28 rows in the DataFrame
------------------------------------------------------


0
_id                       64979bb5667ad5b134bd871f
FHRSID                                      110681
ChangesByServerID                                0
LocalAuthorityBusinessID                      4029
BusinessName                   The Chase Rest Home
BusinessType                       Caring Premises
BusinessTypeID                                   5
AddressLine1                  5-6 Southfields Road
AddressLine2                            Eastbourne
AddressLine3                           East Sussex

### 2. Which establishments in London have a `RatingValue` greater than or equal to 4?

In [9]:
# Find the establishments with London as the Local Authority and has a RatingValue greater than or equal to 4.
query_02 = {'LocalAuthorityName': {'$regex':'London'},'RatingValue':{'$gte':4}}
results_02 = establishments.find(query_02)


# Use count_documents to display the number of documents in the result
print('------------------------------------------------------')

print(f'There are  {establishments.count_documents(query_02)} documents in the results with London as the \
      Local Authority and have a RatingValue greater than or equal to 4 ')

print('------------------------------------------------------')
# Display the first document in the results using pprint
print('Here is the first document in the results')
print('------------------------------------------------------')
pprint(results_02[0])

------------------------------------------------------
There are  33 documents in the results with London as the       Local Authority and have a RatingValue greater than or equal to 4 
------------------------------------------------------
Here is the first document in the results
------------------------------------------------------
{'AddressLine1': 'Oak Apple Farm Building 103 Sheernes Docks',
 'AddressLine2': 'Sheppy Kent',
 'AddressLine3': '',
 'AddressLine4': '',
 'BusinessName': "Charlie's",
 'BusinessType': 'Other catering premises',
 'BusinessTypeID': 7841,
 'ChangesByServerID': 0,
 'Distance': 4627.439467780196,
 'FHRSID': 621707,
 'LocalAuthorityBusinessID': 'PI/000025307',
 'LocalAuthorityCode': '508',
 'LocalAuthorityEmailAddress': 'publicprotection@cityoflondon.gov.uk',
 'LocalAuthorityName': 'City of London Corporation',
 'LocalAuthorityWebSite': 'http://www.cityoflondon.gov.uk/Corporation/homepage.htm',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'ME12',
 'R

In [158]:
# Convert the result to a Pandas DataFrame
#Creating list from keys and values in dictionary results
inputdict_02 = results_02[0]
columns_02 = list(inputdict_02.keys())
values_list_02 = list(inputdict_02.values())
#converting list to DataFrame
establishments_df_02 = pd.DataFrame(values_list_02,columns_02)

# Display the number of rows in the DataFrame
print(f'There are {len(establishments_df_02.index)} rows in the DataFrame')
print('------------------------------------------------------')
# Display the first 10 rows of the DataFrame
establishments_df_02.head(10)

There are 28 rows in the DataFrame
------------------------------------------------------


0
_id                                         64979bb6667ad5b134bda13b
FHRSID                                                        621707
ChangesByServerID                                                  0
LocalAuthorityBusinessID                                PI/000025307
BusinessName                                               Charlie's
BusinessType                                 Other catering premises
BusinessTypeID                                                  7841
AddressLine1              Oak Apple Farm Building 103 Sheernes Docks
AddressLine2                                             Sheppy Kent
AddressLine3

### 3. What are the top 5 establishments with a `RatingValue` rating value of 5, sorted by lowest hygiene score, nearest to the new restaurant added, "Penang Flavours"?

In [26]:
# Search within 0.01 degree on either side of the latitude and longitude.
# Rating value must equal 5
# Sort by hygiene score

degree_search = 0.01
latitude = establishments.find({'BusinessName':'Penang Flavours'},{'geocode.latitude':1})
longitude = establishments.find({'BusinessName':'Penang Flavours'},{'geocode.longitude':1})

for lat in latitude:
    #print(lat['geocode']['latitude'] +.01)
    latitude_upper = lat['geocode']['latitude'] +0.1
    latitude_lower = lat['geocode']['latitude'] - 0.1
for lon in longitude:
    longitude_upper = lon['geocode']['longitude'] +0.1
    longitude_lower = lon['geocode']['longitude'] - 0.1

# write query for RatingValue and distance query
query = {'$match':{
    'RatingValue': 5,
    'geocode.latitude': {'$gte': latitude_lower, '$lte': latitude_upper},
    'geocode.longitude': {'$gte': longitude_lower, '$lte': longitude_upper}
}}
                
# Create a dictionary that will allow the pipeline to sort by count in descending order
sort = {'$sort': {'scores.Hygiene': -1}}

#limit to limit the results to 5
limit = 5
# Put the pipeline together
pipeline = [query,sort]
    
                          
# Run the pipeline through the aggregate method and save the results to a variable
results_03 = list(establishments.aggregate(pipeline))
# Print the results
pprint(results_03)
                                         

[{'AddressLine1': 'Christ Church Centre',
  'AddressLine2': 'Kingswood Avenue',
  'AddressLine3': 'Swanley',
  'AddressLine4': 'KENT',
  'BusinessName': 'Swanley Kindergarten Pre-school',
  'BusinessType': 'Caring Premises',
  'BusinessTypeID': 5,
  'ChangesByServerID': 0,
  'Distance': 4640.311011978085,
  'FHRSID': 647170,
  'LocalAuthorityBusinessID': '14/00041/MIXED/S',
  'LocalAuthorityCode': '187',
  'LocalAuthorityEmailAddress': 'environmental.health@sevenoaks.gov.uk',
  'LocalAuthorityName': 'Sevenoaks',
  'LocalAuthorityWebSite': 'http://www.sevenoaks.gov.uk/',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'BR8 8AN',
  'RatingDate': '2022-03-14T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb7667ad5b134bdc483'),
  'geocode': {'latitude': 51.39568, 'longitude': 0.182274},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/647170',
             'rel': 'self'}],
  'm

  'BusinessName': 'Tea On The Pantiles',
  'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'ChangesByServerID': 0,
  'Distance': 4644.652058624046,
  'FHRSID': 858515,
  'LocalAuthorityBusinessID': '16/00025/CP',
  'LocalAuthorityCode': '503',
  'LocalAuthorityEmailAddress': 'food.safety@bexley.gov.uk',
  'LocalAuthorityName': 'Bexley',
  'LocalAuthorityWebSite': 'http://www.bexley.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'DA7 5HD',
  'RatingDate': '2018-05-11T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb8667ad5b134bdd482'),
  'geocode': {'latitude': 51.473235, 'longitude': 0.141334},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/858515',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T00:00:00',
           'itemCount': 0,
           'pageNumber': 0,
           'pageSize': 0,
     

  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/1226267',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T00:00:00',
           'itemCount': 0,
           'pageNumber': 0,
           'pageSize': 0,
           'returncode': None,
           'totalCount': 0,
           'totalPages': 0},
  'scores': {'ConfidenceInManagement': 5, 'Hygiene': 5, 'Structural': 5}},
 {'AddressLine1': 'The Crown And Anchor',
  'AddressLine2': '19 Park Road',
  'AddressLine3': 'Bromley',
  'AddressLine4': '',
  'BusinessName': 'Crown And Anchor',
  'BusinessType': 'Pub/bar/nightclub',
  'BusinessTypeID': 7843,
  'ChangesByServerID': 0,
  'Distance': 4646.639037149568,
  'FHRSID': 357501,
  'LocalAuthorityBusinessID': '00000/0000/6/612',
  'LocalAuthorityCode': '505',
  'LocalAuthorityEmailAddress': 'food@bromley.gov.uk',
  'LocalAuthorityName': 'Bromley',
  'LocalAuthorityWebSite': 'http://www.bromley.gov.uk',
  'NewRatingPending': False,
  '

  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T00:00:00',
           'itemCount': 0,
           'pageNumber': 0,
           'pageSize': 0,
           'returncode': None,
           'totalCount': 0,
           'totalPages': 0},
  'scores': {'ConfidenceInManagement': 5, 'Hygiene': 5, 'Structural': 5}},
 {'AddressLine1': '76-78 North Street',
  'AddressLine2': 'Romford',
  'AddressLine3': '',
  'AddressLine4': '',
  'BusinessName': 'Opera Restaurant',
  'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'ChangesByServerID': 0,
  'Distance': 4647.254109693057,
  'FHRSID': 924440,
  'LocalAuthorityBusinessID': '132628',
  'LocalAuthorityCode': '516',
  'LocalAuthorityEmailAddress': 'environmental.health@havering.gov.uk',
  'LocalAuthorityName': 'Havering',
  'LocalAuthorityWebSite': 'http://www.havering.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'RM1 1DA',
  'RatingDate': '2019-09-13T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  '

 {'AddressLine1': '64 Powis Street',
  'AddressLine2': '',
  'AddressLine3': 'Woolwich',
  'AddressLine4': 'Greenwich',
  'BusinessName': 'Greggs',
  'BusinessType': 'Retailers - other',
  'BusinessTypeID': 4613,
  'ChangesByServerID': 0,
  'Distance': 4648.060529950176,
  'FHRSID': 694653,
  'LocalAuthorityBusinessID': 'PI/000119253',
  'LocalAuthorityCode': '511',
  'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
  'LocalAuthorityName': 'Greenwich',
  'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'SE18 6LQ',
  'RatingDate': '2021-10-09T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bde4d8'),
  'geocode': {'latitude': 51.4916395, 'longitude': 0.0663749},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/694653',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'e

...

  'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'SE7 7SW',
  'RatingDate': '2022-01-27T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdeba7'),
  'geocode': {'latitude': 51.4908485412598, 'longitude': 0.0255619995296001},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/695629',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T00:00:00',
           'itemCount': 0,
           'pageNumber': 0,
           'pageSize': 0,
           'returncode': None,
           'totalCount': 0,
           'totalPages': 0},
  'scores': {'ConfidenceInManagement': 0, 'Hygiene': 0, 'Structural': 5}},
 {'AddressLine1': '',
  'AddressLine2': '56-60 Tanner Street',
  'AddressLine3': '',
  'AddressLine4': 'Barking',
  'BusinessName': 'Barking Park Hotel Ltd',
  'BusinessType': 

 {'AddressLine1': '333 Barking Road',
  'AddressLine2': 'East Ham',
  'AddressLine3': 'London',
  'AddressLine4': '',
  'BusinessName': 'Reggae Reggae Pot',
  'BusinessType': 'Takeaway/sandwich shop',
  'BusinessTypeID': 7844,
  'ChangesByServerID': 0,
  'Distance': 4650.074846533256,
  'FHRSID': 1217978,
  'LocalAuthorityBusinessID': '20/00009/FOOD',
  'LocalAuthorityCode': '525',
  'LocalAuthorityEmailAddress': 'food@newham.gov.uk',
  'LocalAuthorityName': 'Newham',
  'LocalAuthorityWebSite': 'https://www.newham.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'E6 1LA',
  'RatingDate': '2020-03-16T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdedee'),
  'geocode': {'latitude': 51.53303, 'longitude': 0.052724},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/1217978',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDa

 {'AddressLine1': '36 - 40 Barking Road',
  'AddressLine2': 'East Ham',
  'AddressLine3': 'London',
  'AddressLine4': '',
  'BusinessName': 'Tesco',
  'BusinessType': 'Retailers - supermarkets/hypermarkets',
  'BusinessTypeID': 7840,
  'ChangesByServerID': 0,
  'Distance': 4650.445350358774,
  'FHRSID': 640326,
  'LocalAuthorityBusinessID': '09/00422/FOOD',
  'LocalAuthorityCode': '525',
  'LocalAuthorityEmailAddress': 'food@newham.gov.uk',
  'LocalAuthorityName': 'Newham',
  'LocalAuthorityWebSite': 'https://www.newham.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'E6 3BP',
  'RatingDate': '2018-11-12T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdf06c'),
  'geocode': {'latitude': 51.5303415, 'longitude': 0.0398539},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/640326',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'e

 {'AddressLine1': '257 Barking Road',
  'AddressLine2': 'Plaistow',
  'AddressLine3': 'London',
  'AddressLine4': '',
  'BusinessName': 'Southern Fried Chicken',
  'BusinessType': 'Takeaway/sandwich shop',
  'BusinessTypeID': 7844,
  'ChangesByServerID': 0,
  'Distance': 4650.884477678035,
  'FHRSID': 640560,
  'LocalAuthorityBusinessID': '12/00151/FOOD',
  'LocalAuthorityCode': '525',
  'LocalAuthorityEmailAddress': 'food@newham.gov.uk',
  'LocalAuthorityName': 'Newham',
  'LocalAuthorityWebSite': 'https://www.newham.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'E13 8EQ',
  'RatingDate': '2019-06-12T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdf348'),
  'geocode': {'latitude': 51.520354, 'longitude': 0.017775},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/640560',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extr

 {'AddressLine1': '48 Romford Road',
  'AddressLine2': 'Stratford',
  'AddressLine3': 'London',
  'AddressLine4': '',
  'BusinessName': 'Taza',
  'BusinessType': 'Retailers - other',
  'BusinessTypeID': 4613,
  'ChangesByServerID': 0,
  'Distance': 4652.0975717597175,
  'FHRSID': 765269,
  'LocalAuthorityBusinessID': '14/01009/FOOD',
  'LocalAuthorityCode': '525',
  'LocalAuthorityEmailAddress': 'food@newham.gov.uk',
  'LocalAuthorityName': 'Newham',
  'LocalAuthorityWebSite': 'https://www.newham.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'E15 4BZ',
  'RatingDate': '2020-02-21T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdf7f4'),
  'geocode': {'latitude': 51.542115, 'longitude': 0.006349},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/765269',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T

In [161]:
# Convert result to Pandas DataFrame
#Creating list from keys and values in dictionary results
inputdict_03 = results_03[0]
columns_03 = list(inputdict_03.keys())
values_list_03 = list(inputdict_03.values())
#converting list to DataFrame
establishments_df_03 = pd.DataFrame(values_list_03,columns_03)

establishments_df_03.head(10)

0
_id                              64979bb7667ad5b134bdc483
FHRSID                                             647170
ChangesByServerID                                       0
LocalAuthorityBusinessID                 14/00041/MIXED/S
BusinessName              Swanley Kindergarten Pre-school
BusinessType                              Caring Premises
BusinessTypeID                                          5
AddressLine1                         Christ Church Centre
AddressLine2                             Kingswood Avenue
AddressLine3                                      Swanley

### 4. How many establishments in each Local Authority area have a hygiene score of 0?

In [198]:
# Create a pipeline that: 
# 1. Matches establishments with a hygiene score of 0
match_query = {'$match':{'scores.Hygiene':0}}
# 2. Groups the matches by Local Authority
group_query = {'$group': {'_id': "$LocalAuthorityName", 'count': { '$sum': 1 }}}
# 3. Sorts the matches from highest to lowest
sort_values = {'$sort':{'count':-1}}

#create pipeline
pipeline = [match_query,group_query,sort_values]
#write aggregate query
results_04 = list(establishments.aggregate(pipeline))

#use len to find the count of documents in results
count = len(list(results_04))

# Print the number of documents in the result
print(f'There are {count} documents in the results')

print('-----------------------------------------')

print('The following are the counts of Local Authorities with hygiene score of 0')
print('-----------------------------------------')
# Print the first 10 results
pprint(results_04[0:10])
results_df_04 = results_04[0:10]

There are 55 documents in the results
-----------------------------------------
The following are the counts of Local Authorities with hygiene score of 0
-----------------------------------------
[{'_id': 'Thanet', 'count': 1130},
 {'_id': 'Greenwich', 'count': 882},
 {'_id': 'Maidstone', 'count': 713},
 {'_id': 'Newham', 'count': 711},
 {'_id': 'Swale', 'count': 686},
 {'_id': 'Chelmsford', 'count': 680},
 {'_id': 'Medway', 'count': 672},
 {'_id': 'Bexley', 'count': 607},
 {'_id': 'Southend-On-Sea', 'count': 586},
 {'_id': 'Tendring', 'count': 542}]


In [199]:
# Convert the result to a Pandas DataFrame

establishments_df_04 = pd.DataFrame(results_df_04)

# Display the number of rows in the DataFrame
print(f'There are {len(establishments_df_04.index)} rows in the DataFrame')
print('------------------------------------------------------')
# Display the first 10 rows of the DataFrame
establishments_df_04.head(10)

There are 10 rows in the DataFrame
------------------------------------------------------


_id  count
0           Thanet   1130
1        Greenwich    882
2        Maidstone    713
3           Newham    711
4            Swale    686
5       Chelmsford    680
6           Medway    672
7           Bexley    607
8  Southend-On-Sea    586
9         Tendring    542